In [0]:
from pyspark.sql import functions as F, types as T
from pyspark.sql.window import Window

In [0]:
deliveries_df = spark.read.format("csv") \
    .option("header","true") \
    .load("/FileStore/tables/deliveries.csv")


deliveries_df.show()

+--------+------+--------------------+--------------------+----+----+-----------+---------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+-------+
|match_id|inning|        batting_team|        bowling_team|over|ball|     batter|   bowler|non_striker|batsman_runs|extra_runs|total_runs|extras_type|is_wicket|player_dismissed|dismissal_kind|fielder|
+--------+------+--------------------+--------------------+----+----+-----------+---------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+-------+
|  335982|     1|Kolkata Knight Ri...|Royal Challengers...|   0|   1| SC Ganguly|  P Kumar|BB McCullum|           0|         1|         1|    legbyes|        0|              NA|            NA|     NA|
|  335982|     1|Kolkata Knight Ri...|Royal Challengers...|   0|   2|BB McCullum|  P Kumar| SC Ganguly|           0|         0|         0|       NULL|        0|              NA|            NA|    

In [0]:
deliveries_df.select('match_id').distinct().sort(F.col('match_id').desc()).show()

+--------+
|match_id|
+--------+
|  981019|
|  981017|
|  981015|
|  981013|
|  981011|
|  981009|
|  981007|
|  981005|
|  981003|
|  981001|
|  980999|
|  980997|
|  980995|
|  980993|
|  980991|
|  980989|
|  980987|
|  980985|
|  980983|
|  980981|
+--------+
only showing top 20 rows



In the above frame, when the matchid was sorted in descending order, it was not sorted properly because the datatype of the matchid column was string as shown below.

In [0]:
deliveries_df.printSchema()

root
 |-- match_id: string (nullable = true)
 |-- inning: string (nullable = true)
 |-- batting_team: string (nullable = true)
 |-- bowling_team: string (nullable = true)
 |-- over: string (nullable = true)
 |-- ball: string (nullable = true)
 |-- batter: string (nullable = true)
 |-- bowler: string (nullable = true)
 |-- non_striker: string (nullable = true)
 |-- batsman_runs: string (nullable = true)
 |-- extra_runs: string (nullable = true)
 |-- total_runs: string (nullable = true)
 |-- extras_type: string (nullable = true)
 |-- is_wicket: string (nullable = true)
 |-- player_dismissed: string (nullable = true)
 |-- dismissal_kind: string (nullable = true)
 |-- fielder: string (nullable = true)



Convert all the integer columns to IntegerType datatype and string columns to StringType datatype.

In [0]:
int_cols = ['match_id', 'inning', 'over', 'ball', 'batsman_runs', 'extra_runs', 'total_runs', 'is_wicket']

fields = [T.StructField(col, T.IntegerType(), nullable=True) if col in int_cols 
          else T.StructField(col, T.StringType(), nullable=True) for col in deliveries_df.columns]

In [0]:
fields

[StructField('match_id', IntegerType(), True),
 StructField('inning', IntegerType(), True),
 StructField('batting_team', StringType(), True),
 StructField('bowling_team', StringType(), True),
 StructField('over', IntegerType(), True),
 StructField('ball', IntegerType(), True),
 StructField('batter', StringType(), True),
 StructField('bowler', StringType(), True),
 StructField('non_striker', StringType(), True),
 StructField('batsman_runs', IntegerType(), True),
 StructField('extra_runs', IntegerType(), True),
 StructField('total_runs', IntegerType(), True),
 StructField('extras_type', StringType(), True),
 StructField('is_wicket', IntegerType(), True),
 StructField('player_dismissed', StringType(), True),
 StructField('dismissal_kind', StringType(), True),
 StructField('fielder', StringType(), True)]

In [0]:
deliveries_df = spark.read.format("csv") \
    .option("header","true") \
    .schema(T.StructType(fields)) \
    .load("/FileStore/tables/deliveries.csv")

deliveries_df.display()

match_id inning batting_team bowling_team over ball batter bowler non_striker batsman_runs extra_runs total_runs extras_type is_wicket player_dismissed dismissal_kind fielder 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 1 SC Ganguly P Kumar BB McCullum 0 1 1 legbyes 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 2 BB McCullum P Kumar SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 3 BB McCullum P Kumar SC Ganguly 0 1 1 wides 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 4 BB McCullum P Kumar SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 5 BB McCullum P Kumar SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 6 BB McCullum P Kumar SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 0 7 BB McCullum P Kumar SC Ganguly 0 1 1 legbyes 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 1 BB McCullum Z Khan SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 2 BB McCullum Z Khan SC Ganguly 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 3 BB McCullum Z Khan SC Ganguly 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 4 BB McCullum Z Khan SC Ganguly 6 0 6 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 5 BB McCullum Z Khan SC Ganguly 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 1 6 BB McCullum Z Khan SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 1 SC Ganguly P Kumar BB McCullum 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 2 SC Ganguly P Kumar BB McCullum 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 3 SC Ganguly P Kumar BB McCullum 0 1 1 legbyes 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 4 BB McCullum P Kumar SC Ganguly 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 5 BB McCullum P Kumar SC Ganguly 1 0 1 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 2 6 SC Ganguly P Kumar BB McCullum 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 1 BB McCullum AA Noffke SC Ganguly 0 5 5 wides 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 2 BB McCullum AA Noffke SC Ganguly 6 0 6 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 3 BB McCullum AA Noffke SC Ganguly 0 1 1 legbyes 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 4 SC Ganguly AA Noffke BB McCullum 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 5 SC Ganguly AA Noffke BB McCullum 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 6 SC Ganguly AA Noffke BB McCullum 1 0 1 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 3 7 BB McCullum AA Noffke SC Ganguly 6 0 6 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 1 SC Ganguly P Kumar BB McCullum 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 2 SC Ganguly P Kumar BB McCullum 1 0 1 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 3 BB McCullum P Kumar SC Ganguly 4 0 4 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 4 BB McCullum P Kumar SC Ganguly 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 5 BB McCullum P Kumar SC Ganguly 1 0 1 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 4 6 SC Ganguly P Kumar BB McCullum 0 0 0 null 0 NA NA NA 335982 1 Kolkata Knight Riders Royal Challengers Bangalore 5 1 BB McCullum Z Khan SC Gangul

In [0]:
deliveries_df.printSchema()

root
 |-- match_id: integer (nullable = true)
 |-- inning: integer (nullable = true)
 |-- batting_team: string (nullable = true)
 |-- bowling_team: string (nullable = true)
 |-- over: integer (nullable = true)
 |-- ball: integer (nullable = true)
 |-- batter: string (nullable = true)
 |-- bowler: string (nullable = true)
 |-- non_striker: string (nullable = true)
 |-- batsman_runs: integer (nullable = true)
 |-- extra_runs: integer (nullable = true)
 |-- total_runs: integer (nullable = true)
 |-- extras_type: string (nullable = true)
 |-- is_wicket: integer (nullable = true)
 |-- player_dismissed: string (nullable = true)
 |-- dismissal_kind: string (nullable = true)
 |-- fielder: string (nullable = true)



In [0]:
deliveries_df.select('match_id').distinct().sort(F.col('match_id').desc()).show()

+--------+
|match_id|
+--------+
| 1426312|
| 1426311|
| 1426310|
| 1426309|
| 1426307|
| 1426306|
| 1426305|
| 1426303|
| 1426302|
| 1426300|
| 1426299|
| 1426298|
| 1426297|
| 1426296|
| 1426295|
| 1426294|
| 1426293|
| 1426292|
| 1426291|
| 1426290|
+--------+
only showing top 20 rows



In [0]:
ipl_final_df = deliveries_df.filter(F.col('match_id') == 1426312)

ipl_final_df.show()

+--------+------+-------------------+--------------------+----+----+---------------+--------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+------------------+
|match_id|inning|       batting_team|        bowling_team|over|ball|         batter|  bowler|non_striker|batsman_runs|extra_runs|total_runs|extras_type|is_wicket|player_dismissed|dismissal_kind|           fielder|
+--------+------+-------------------+--------------------+----+----+---------------+--------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+------------------+
| 1426312|     1|Sunrisers Hyderabad|Kolkata Knight Ri...|   0|   1|Abhishek Sharma|MA Starc|    TM Head|           0|         0|         0|       NULL|        0|              NA|            NA|                NA|
| 1426312|     1|Sunrisers Hyderabad|Kolkata Knight Ri...|   0|   2|Abhishek Sharma|MA Starc|    TM Head|           0|         0|         0|    

In [0]:
first_innings_batting = ipl_final_df.filter(F.col('inning') == 1)

first_innings_batting.show()

+--------+------+-------------------+--------------------+----+----+---------------+--------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+------------------+
|match_id|inning|       batting_team|        bowling_team|over|ball|         batter|  bowler|non_striker|batsman_runs|extra_runs|total_runs|extras_type|is_wicket|player_dismissed|dismissal_kind|           fielder|
+--------+------+-------------------+--------------------+----+----+---------------+--------+-----------+------------+----------+----------+-----------+---------+----------------+--------------+------------------+
| 1426312|     1|Sunrisers Hyderabad|Kolkata Knight Ri...|   0|   1|Abhishek Sharma|MA Starc|    TM Head|           0|         0|         0|       NULL|        0|              NA|            NA|                NA|
| 1426312|     1|Sunrisers Hyderabad|Kolkata Knight Ri...|   0|   2|Abhishek Sharma|MA Starc|    TM Head|           0|         0|         0|    

In [0]:
scorecard_df = first_innings_batting.filter(F.col('extras_type').isNull()).groupBy(F.col('batter')) \
    .agg(F.sum(F.col('batsman_runs')).alias('runs'), 
    F.count((F.col('ball'))).alias('balls'),
    F.count(F.when(first_innings_batting.batsman_runs == 4, 1)).alias('4s'),
    F.count(F.when(first_innings_batting.batsman_runs == 6, 1)).alias('6s'),
    F.round(F.sum('batsman_runs')*100/F.count('ball'), 2).alias('S/R')
    )

scorecard_df.show()

+-------------------+----+-----+---+---+------+
|             batter|runs|balls| 4s| 6s|   S/R|
+-------------------+----+-----+---+---+------+
|            B Kumar|   0|    1|  0|  0|   0.0|
|         JD Unadkat|   4|   11|  0|  0| 36.36|
|          H Klaasen|  16|   17|  1|  0| 94.12|
|            TM Head|   0|    1|  0|  0|   0.0|
|        Abdul Samad|   4|    4|  0|  0| 100.0|
|    Abhishek Sharma|   2|    5|  0|  0|  40.0|
|Nithish Kumar Reddy|  13|   10|  1|  1| 130.0|
|      Shahbaz Ahmed|   8|    7|  0|  1|114.29|
|         AK Markram|  20|   23|  3|  0| 86.96|
|         PJ Cummins|  24|   17|  2|  1|141.18|
|        RA Tripathi|   9|   12|  1|  0|  75.0|
+-------------------+----+-----+---+---+------+



In [0]:
batsman_order = first_innings_batting.withColumn('over-ball', (F.concat(F.col("over"), F.lit("."), F.col("ball"))).cast(T.FloatType())).groupBy("batter").agg(F.min("over-ball").alias("order")).orderBy("order")

batsman_order.show()

+-------------------+-----+
|             batter|order|
+-------------------+-----+
|    Abhishek Sharma|  0.1|
|        RA Tripathi|  0.6|
|            TM Head|  1.6|
|         AK Markram|  2.3|
|Nithish Kumar Reddy|  4.3|
|          H Klaasen|  7.3|
|      Shahbaz Ahmed| 10.3|
|        Abdul Samad| 11.6|
|         PJ Cummins| 12.6|
|         JD Unadkat| 14.2|
|            B Kumar| 17.6|
+-------------------+-----+



In [0]:
batsman_order = batsman_order.withColumn("batting_order", F.row_number().over(Window.orderBy("order")))
batsman_order.show()

+-------------------+-----+-------------+
|             batter|order|batting_order|
+-------------------+-----+-------------+
|    Abhishek Sharma|  0.1|            1|
|        RA Tripathi|  0.6|            2|
|            TM Head|  1.6|            3|
|         AK Markram|  2.3|            4|
|Nithish Kumar Reddy|  4.3|            5|
|          H Klaasen|  7.3|            6|
|      Shahbaz Ahmed| 10.3|            7|
|        Abdul Samad| 11.6|            8|
|         PJ Cummins| 12.6|            9|
|         JD Unadkat| 14.2|           10|
|            B Kumar| 17.6|           11|
+-------------------+-----+-------------+



In [0]:
final_scorecard = scorecard_df.join(batsman_order, on=['batter', 'batter'], how='inner')

final_scorecard.select('batter', 'runs', 'balls', '4s', '6s', 'S/R').orderBy(F.col('order')).show()

+-------------------+----+-----+---+---+------+
|             batter|runs|balls| 4s| 6s|   S/R|
+-------------------+----+-----+---+---+------+
|    Abhishek Sharma|   2|    5|  0|  0|  40.0|
|        RA Tripathi|   9|   12|  1|  0|  75.0|
|            TM Head|   0|    1|  0|  0|   0.0|
|         AK Markram|  20|   23|  3|  0| 86.96|
|Nithish Kumar Reddy|  13|   10|  1|  1| 130.0|
|          H Klaasen|  16|   17|  1|  0| 94.12|
|      Shahbaz Ahmed|   8|    7|  0|  1|114.29|
|        Abdul Samad|   4|    4|  0|  0| 100.0|
|         PJ Cummins|  24|   17|  2|  1|141.18|
|         JD Unadkat|   4|   11|  0|  0| 36.36|
|            B Kumar|   0|    1|  0|  0|   0.0|
+-------------------+----+-----+---+---+------+

